In [1]:
!pip install transformers datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 566.1/566.1 kB 14.6 MB/s eta 0:00:0000:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.7/47.7 MB 37.3 MB/s eta 0:00:00:00:0100:01
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 19.0.1
    Uninstalling pyarrow-19.0.1:
      Successfully uninstalled pyarrow-19.0.1
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 1.0.0rc2
    Uninstalling huggingface-hub-1.0.0rc2:
      Successfully uninstalled huggingface-hub-1.0.0rc2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigframes 2.12.0 requires google-cloud-bigquery-storage<3.0.0,>=2.30.0, which is not installed.
pylibcudf-cu12 25.2.2 requires pyarrow<20.0.0a0,>=14.0.0; platform_machine == "x86_64", but you have pyarrow 22.0.0 which is incompatible.
cudf-cu12 25.2.2 requires pyarrow<20.0.0a0,>=14.0.0; platf

In [2]:
from huggingface_hub import login
login()

In [3]:
import csv
import os
from tqdm import tqdm
import uuid
import shutil

from transformers import pipeline
import scipy
from IPython.display import Audio

import torch
import torchaudio
import soundfile as sf

2025-11-17 14:37:34.297298: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1763390254.477207      39 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1763390254.528241      39 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## Tasty MusicGen Model

In [4]:
synthesiser = pipeline("text-to-audio", "csc-unipd/tasty-musicgen-small")

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/2.36G [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'repr' attribute with value False was provided to the `Field()` function, which has no effect in the context it was used. 'repr' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` statement was used, or if the `Field()` function was attached to a single member of a union type.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'frozen' attribute with value True was provided to the `Field()` function, which has no effect in the context it was used. 'frozen' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` 

generation_config.json:   0%|          | 0.00/224 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

Device set to use cuda:0


# Generate audio with prompts

In [8]:
prompt = "Lead with a chill electric guitar as the melodic pillar, selecting a bright, glassy timbre and a mid-to-high pitch contour whose energy climbs from a soothing, refreshing baseline to an upbeat, lively arc, mapping color descriptors to timbre and pitch while letting happiness, surprise, refreshing, light, and spicy guide articulation (crisp staccato on off-beats, swift legato phrases) and rhythmic accents with dynamic swells to shape the melodic profile. With the captions (emotion: surprise; emotion: happiness; texture: refreshing; texture: light; taste: spicy) and a bright temperature descriptor, craft one harmonious layer using secondary instruments (piano and a warm pad) that is consonant and uplifting, selecting a I–VI–IV–V-like progression that supports the melody and ensures the combined texture is clearly audible within the first 30 seconds."
music = synthesiser(prompt, forward_params={"do_sample": True})
Audio(data=music["audio"].squeeze(), rate=music["sampling_rate"])

In [9]:
prompt = "A bright electric guitar leads with a rapid, staccato major-scale melody featuring sharp timbral attack and joyful ascending pitch contours, its energetic syncopated rhythm and dynamic swells reflecting spicy-hot zest within a light, refreshing texture. Within the first thirty seconds, airy synth-pad harmonies and subtle percussive accents reinforce this cheerful melody, orchestrating surprise-infused major chords that blend lively articulation with happiness-driven harmonic support."
music = synthesiser(prompt, forward_params={"do_sample": True})
Audio(data=music["audio"].squeeze(), rate=music["sampling_rate"])

In [5]:
def music_reprompts(filepath: str) -> list[[dict[str, str]]]:
    with open(filepath, 'r') as file_:
        reader = csv.DictReader(file_)
        prompts = [row for row in reader]

    return prompts


def generate_using_reprompts(prompts: list[dict[str, str]], output_dir: str, raw_prompt: bool = False):
    os.makedirs(output_dir, exist_ok=True)
    field = 'reprompt' if raw_prompt else 'prompt'
    for prompt in tqdm(prompts, desc='audio generation progress'):
        music = synthesiser(prompt[field], forward_params={"do_sample": True})
        id_prompt = str(uuid.uuid4())[:8] if 'id_prompt' not in prompt else prompt['id_prompt']
        scipy.io.wavfile.write(f"{output_dir}/{id_prompt}.wav", rate=music["sampling_rate"], data=music["audio"])


## Exploration audio generation with Kimi-K2 and GPT5-Nano prompts

In [25]:
kimi_k2_prompts = music_reprompts('/kaggle/input/kimi-reprompt-k2/pipeline_results_kimi_k2_3_prompt_v2.csv')
generate_using_reprompts(kimi_k2_prompts, '/kaggle/working/kimi_audios_v2')
shutil.make_archive('kimi_audios', 'zip', '/kaggle/working/kimi_audios_v2')
shutil.rmtree('kimi_audios_v2')

audio generation progress: 100%|██████████| 3/3 [01:40<00:00, 33.38s/it]


'/kaggle/working/kimi_audios.zip'

In [26]:
nano_prompts = music_reprompts('/kaggle/input/gpt5-nano/pipeline_results_gpt5_nano_3_prompt_v2.csv')
generate_using_reprompts(nano_prompts, '/kaggle/working/nano_audios_v2')
shutil.make_archive('nano_audios', 'zip', '/kaggle/working/nano_audios_v2')
shutil.rmtree('nano_audios_v2')

audio generation progress: 100%|██████████| 3/3 [01:40<00:00, 33.60s/it]


'/kaggle/working/nano_audios.zip'

## Audio Generation for 50 prompts

### GPT5-Nano Prompt V2

In [31]:
nano_prompts = music_reprompts('/kaggle/input/nano-50-v2/pipeline_results_gpt5_nano_50_prompt_v2.csv')
generate_using_reprompts(nano_prompts, '/kaggle/working/nano_audios_50_v2')
shutil.make_archive('nano_audios_50', 'zip', '/kaggle/working/nano_audios_50_v2')
shutil.rmtree('nano_audios_50_v2')

audio generation progress: 100%|██████████| 50/50 [28:39<00:00, 34.39s/it]


### Kimi-K2 Prompt V2

In [10]:
kimi_prompts = music_reprompts('/kaggle/input/kimi-k2-50/pipeline_results_kimi_k2_50_prompt_v2.csv')
generate_using_reprompts(kimi_prompts, '/kaggle/working/kimi_audios_50_v2', )
shutil.make_archive('kimi_audios_50', 'zip', '/kaggle/working/kimi_audios_50_v2')
shutil.rmtree('kimi_audios_50_v2')

audio generation progress: 100%|██████████| 50/50 [28:18<00:00, 33.98s/it]


### Audios de Validación Final

#### Kimi K2 con Reprompt (V3)

In [6]:
kimi_prompts = music_reprompts('/kaggle/input/prompts-v3/pipeline_results_kimi_k2_thinking_50_prompt_v3.csv')
generate_using_reprompts(kimi_prompts, '/kaggle/working/kimi_audios_50_v3')
shutil.make_archive('kimi_audios_50', 'zip', '/kaggle/working/kimi_audios_50_v3')
shutil.rmtree('kimi_audios_50_v3')

audio generation progress: 100%|██████████| 50/50 [27:41<00:00, 33.24s/it]


#### Usando Raw Prompt

In [7]:
kimi_prompts = music_reprompts('/kaggle/input/prompts-v3/pipeline_results_kimi_k2_thinking_50_prompt_v3.csv')
generate_using_reprompts(kimi_prompts, '/kaggle/working/kimi_audios_50_raw', raw_prompt=True)
shutil.make_archive('kimi_audios_50_raw_prompts', 'zip', '/kaggle/working/kimi_audios_50_raw')
shutil.rmtree('kimi_audios_50_raw')

audio generation progress: 100%|██████████| 50/50 [27:40<00:00, 33.20s/it]


#### Cleanup

In [30]:
# os.remove('kimi_audios.zip')
# os.remove('nano_audios.zip')